In [1]:
import pandas as pd
import numpy as np
from tqdm.notebook import tqdm

import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.io as pio
pio.templates.default = 'plotly_white'

import warnings
warnings.filterwarnings("ignore")

In [2]:
path='/mnt/cephfs/ml_data/mc_2021/'

In [3]:
import pickle

xgbregs = []
xgbregs.append(pickle.load(open("models/16_features_max_depth_10/xgb_energy_ideal_opt_16.dat", "rb")))
xgbregs.append(pickle.load(open("models/16_features_max_depth_10/xgb_energy_real_opt_16.dat", "rb")))

In [4]:
opt_features = ['AccumCharge', 'R_cht', 'z_cc', 'pe_std',
                'nPMTs', 'ht_kurtosis', 'ht_25-20p', 'R_cc',
                'ht_5-2p', 'pe_mean', 'jacob_cht', 'phi_cc',
                'ht_35-30p', 'ht_20-15p', 'pe_35p', 'ht_30-25p']

# Surface

In [5]:
%%time
Rs = [0, 8.0, 10.1, 11.5, 12.7, 13.7, 14.5, 15.3, 16.0, 16.6, 17.2]
energies = [0, 0.1, 0.3, 0.6] + list(range(1, 11))

y_true_all = []
y_pred_all = []
for k in tqdm(range(len(Rs)), "Rs...", leave=False):        
    y_true_array = []
    y_pred_array = []
    for j in tqdm(range(len(xgbregs)), "Models...", leave=False):
        if j == 0:
            name = 'ProcessedTestIdeal'
        elif j == 1:
            name = 'ProcessedTestReal'
        y_true = []
        y_pred = []
        for energy in tqdm(energies, "Energies...", leave=False):
            test = pd.read_csv('{}processed_data/{}/{}MeV.csv.gz'.format(path, name, energy))
            if k < len(Rs)-1:
                test = test[test['edepR'] > Rs[k]]
                test = test[test['edepR'] < Rs[k+1]]
            else:
                test = test[test['edepR'] < 17.2]
            edep = np.array(test['edep'])
            X_test = test.iloc[:, :-5][opt_features]
            edep_preds = xgbregs[j].predict(np.array(X_test))

            y_true.append(edep)
            y_pred.append(edep_preds)
            
        y_true_array.append(y_true)
        y_pred_array.append(y_pred)
        
    y_true_all.append(y_true_array)
    y_pred_all.append(y_pred_array)

Rs...:   0%|          | 0/11 [00:00<?, ?it/s]

Models...:   0%|          | 0/2 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Models...:   0%|          | 0/2 [00:00<?, ?it/s]

...

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Models...:   0%|          | 0/2 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

CPU times: user 20min 56s, sys: 10.6 s, total: 21min 6s
Wall time: 17min 39s


In [6]:
diffs = np.array([
    [[y_pred_all[k][j][i] - y_true_all[k][j][i] for i in range(len(y_pred_array[0]))]
    for j in range(len(y_true_all[0]))]
    for k in range(len(y_true_all))
])

In [7]:
energies = [0, 0.1, 0.3, 0.6] + list(range(1, 11))
energies = np.array([1.022+i for i in energies]).round(5)
energies

array([ 1.022,  1.122,  1.322,  1.622,  2.022,  3.022,  4.022,  5.022,
        6.022,  7.022,  8.022,  9.022, 10.022, 11.022])

In [8]:
[diffs[i][0][0].shape for i in range(len(Rs))]

[(9132,),
 (9378,),
 (8883,),
 (9443,),
 (9426,),
 (8636,),
 (9664,),
 (9174,),
 (8580,),
 (9451,),
 (91767,)]

In [9]:
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit
from scipy.stats import norm

a_all = []
errors_all = []
for j in tqdm(range(diffs.shape[0])):
    a_array = []
    errors_array = []
    for k in range(diffs.shape[1]):
        a = []
        e = []
        for i in range(diffs.shape[2]):
            fig, ax = plt.subplots()
            nbins = 150
            n, bins, patches = ax.hist(diffs[j][k][i], nbins, density=True,
                                       facecolor = 'grey', alpha = 0.5, label='before');
            plt.close(fig)
            centers = (0.5*(bins[1:]+bins[:-1]))
            pars, cov = curve_fit(lambda x, mu, sig : norm.pdf(x, loc=mu, scale=sig), centers, n, p0=[0,1])  
            a.append(pars)
            e.append(cov)
        a_array.append(a)
        errors_array.append(e)
    a_all.append(a_array)
    errors_all.append(errors_array)

  0%|          | 0/11 [00:00<?, ?it/s]

In [10]:
names = ['R: {}-{} m'.format(Rs[i], Rs[i+1]) for i in range(len(Rs)-1)]
names += ['R: 0-17.2 m']

In [11]:
# from scipy import stats
# fig = go.Figure()

# ind = 5 # R cut

# for i in range(diffs.shape[2]): 
#     x = np.linspace(diffs[ind][1][i].min(), diffs[ind][1][i].max(), 100)
#     p = stats.norm.pdf(x, a_all[ind][1][i][0], a_all[ind][1][i][1])

#     fig.add_trace(go.Scatter(x=x,
#                  y=p, mode='lines', name='mu={:.3f} +- {:.3f}, sigma={:.3f} +- {:.3f}'.format(
#                      a_all[ind][1][i][0], np.sqrt(errors_all[ind][1][i][0][0]),
#                      a_all[ind][1][i][1], np.sqrt(errors_all[ind][1][i][1][1])),
#                     visible = (i==0)
#                 ))

# for i in range(diffs.shape[2]): 
#     fig.add_trace(go.Histogram(x=diffs[ind][1][i], xbins=dict(size=0.005),
#                   showlegend=False, histnorm='probability density',
#                  visible = (i==0)
#                 ))

# buttons = []
# for N in range(diffs.shape[2]): 
#     buttons.append(
#         dict(
#              args=['visible', [False]*N + [True] + [False]*(diffs.shape[2]-1-N)],
#                  label='Energy =  {} MeV'.format(energies[N]),
#              method='restyle'
#         )
#     )

# fig.update_layout(

#     xaxis = dict(
#         showline=True,
#         ticks='outside',
#         mirror=True,
#         linecolor='black',
#         showgrid=True,
#         gridcolor='grey',
#         gridwidth=0.25,
#     ),

#     yaxis = dict(
#         showline=True,
#         ticks='outside',
#         mirror=True,
#         linecolor='black',
#         tick0=0,
# #             dtick=1,
#         showgrid=True,
#         gridcolor='grey',
#         gridwidth=0.25,
#         zeroline=True,
#         zerolinecolor='black',
#         zerolinewidth=0.25
#         ),
# )


# fig.update_layout(
#     xaxis_title=r"$$E_{rec} - E_{true}$$",
# #         yaxis_title="y",
#     showlegend=True,
#     updatemenus=list([
#         dict(
#             x=0.5,
#             y=1.2,
#             yanchor='top',
#             buttons=buttons
#         ),
#     ]),
#     legend=dict(
#         orientation="h",
#         yanchor="bottom",
#         y=1.05,
#         xanchor="right",
#         x=1
#     )
# )

# fig.show()

In [12]:
error_sigma_all = []
for ind in range(diffs.shape[0]):
    error_sigma = []
    for k in range(diffs.shape[1]):
        error = [100 * np.sqrt(errors_all[ind][k][i][1][1]) / energies[i] for i in range(1, len(energies)-1)]
        error_sigma.append(error)
    error_sigma_all.append(error_sigma)

error_mu_all = []
for ind in range(diffs.shape[0]):
    error_mu = []
    for k in range(diffs.shape[1]):
        error = [100 * np.sqrt(errors_all[ind][k][i][0][0]) / energies[i] for i in range(1, len(energies)-1)]
        error_mu.append(error)
    error_mu_all.append(error_mu)

In [13]:
np.array(errors_all).shape

(11, 2, 14, 2, 2)

In [14]:
res_all = []
bias_all = []
for ind in range(diffs.shape[0]):
    res = []
    bias = []
    for k in range(diffs.shape[1]):
        sigma = [100 * a_all[ind][k][i][1] / energies[i] for i in range(1, len(energies)-1)]
        mu = [100 * a_all[ind][k][i][0] / energies[i] for i in range(1, len(energies)-1)]
        res.append(sigma)
        bias.append(mu)
        
    res_all.append(res)
    bias_all.append(bias)

In [15]:
np.array(res_all).shape

(11, 2, 12)

In [16]:
colors = ['red', 'darkviolet', 'blue', 'green', 'black']*3

In [17]:
names = ['R: {}-{} m'.format(Rs[i], Rs[i+1]) for i in range(len(Rs)-1)]
names += ['R: 0-17.2 m']
leg=False

def plot_results(appr=False, ylim=3.5):
    x_lin = np.linspace(0.8, 11.5, 1000)

    fig = make_subplots(rows=2, cols=2,
                        shared_xaxes=True,
                        vertical_spacing=0.01,
                        row_width=[0.25, 0.75],
                        column_widths=[0.5, 0.5],
                        subplot_titles=("Ideal", "Real")

    )

    for i in range(len(xgbregs)):
        if i==0:
            leg=False
        else:
            leg=True
        for k in range(diffs.shape[0]):
            fig.add_trace(
                go.Scatter(
                    x=energies[1:13],
                    y=res_all[k][i],
                    mode='markers',
                    marker=dict(
                        color=colors[k],
                        symbol=k
                    ),
                    showlegend=leg,
                    error_y=dict(
                        type='data',
                        width=10,
                        array=error_sigma_all[k][i],
                        visible=True
                    ),
                    name=names[k]
                ), row=1, col=i+1
            )

            fig.add_trace(
                go.Scatter(
                    x=energies[1:13],
                    y=bias_all[k][i],
                    mode='markers',
                    showlegend=False,
                    marker=dict(
                        color=colors[k],
                        symbol=k
                    ),
                    error_y=dict(
                            type='data',
                            width=10,
                            array=error_mu_all[k][i],
                            visible=True
                    ),
                    name=names[k]
                ), row=2, col=i+1
            )
            
    if appr:
        for i in range(len(xgbregs)):
            for k in range(len(names)):
                fig.add_trace(
                    go.Scatter(
                        x=x_lin,
                        y=func(x_lin, a[:, i][k], b[:, i][k], c[:, i][k]),
                        mode='lines',
                        line=dict(
                        ),
                        opacity=0.5,
                        showlegend=False,
                        name=names[k],
                        marker=dict(
                            color=colors[k]
                        )
                    ), row=1, col=i+1
                )


    xaxis = dict(
        showline=True,
        ticks='outside',
        mirror=True,
        tick0=1,
        dtick=1,
        linecolor='black',
        showgrid=True,
        gridcolor='grey',
        gridwidth=0.25,
    )

    yaxis = lambda range: dict(
        showline=True,
        ticks='outside',
        mirror=True,
        linecolor='black',
        range=range,
        showgrid=True,
        gridcolor='grey',
        gridwidth=0.25,
        zeroline=True,
        zerolinecolor='black',
        zerolinewidth=0.25
    )

    fig.update_layout(
        xaxis3_title="Visible energy, MeV",
        xaxis4_title="Visible energy, MeV",
        yaxis1_title="Resolution, %",
    #     yaxis2_title="Resolution, %",
        yaxis3_title="Bias, %",
    #     yaxis4_title="Bias, %",

        xaxis1 = xaxis,
        xaxis2 = xaxis,
        xaxis3 = xaxis,
        xaxis4 = xaxis,
        yaxis1 = yaxis([0, ylim]),
        yaxis2 = yaxis([0, ylim]),
        yaxis3 = yaxis([-0.5, 0.5]),
        yaxis4 = yaxis([-0.5, 0.5]),

        showlegend=True,
        height=500,
        width=950,
        font=dict(
                family="Times New Roman",
                size=16,
        ),

        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=1.05,
            xanchor="right",
            x=1,
            title_font_family="Times New Roman",
            font=dict(
                family="Times New Roman",
                size=16,
                color="black"
            ),
        )
    )

    fig.show()
    if appr:
        pio.write_image(
            fig, 'subdetectors/equidistant_subs/plots/appr_compare_results_for_diff_regions.pdf',
            height=500, width=950)
    else:
        pio.write_image(
            fig, 'subdetectors/equidistant_subs/plots/compare_results_for_diff_regions.pdf',
            height=500, width=950)


In [18]:
plot_results()

In [19]:
def a(x, a):
    return np.sqrt((a/x**0.5)**2)


def b(x, b):
    b_list = []
    b_list.append(np.sqrt(b**2))
    return b_list*len(x)


def c(x, c):
    return np.sqrt((c/x)**2)


def func(x, a, b, c):
    return np.sqrt((a/x**0.5)**2 + b**2 + (c/x)**2) 


def approximated(x, y, yerr):
    popt, pcov = curve_fit(func, x, y, sigma=yerr, maxfev=10**8, bounds=([0, 0, 0.25], [5, 5, 5]))
    a, b, c = popt
    #perr = np.sqrt(abs(pcov.diagonal()))

    return func(x, a, b, c), popt, pcov


In [20]:
fig = go.Figure()

fig.add_trace(
    go.Surface(
        x=energies[1:-1],
        y=names[:-1],
        z=np.array(res_all)[:-1, 1, :],
        colorscale='inferno'
    )
)

fig.update_layout(
    autosize=True,
    title="Real",
    scene = dict(
        xaxis_title='Visible energy, MeV',
        yaxis_title='R, m',
        zaxis_title='Resolution, %',
    ),
    width=800,
    height=700
)

fig.show()

In [21]:
from statsmodels.stats.moment_helpers import cov2corr

y_approximated_all = []
coefs_all = []
errors_all = []
corr_matrixes_all = []
for i in range(len(xgbregs)):
    y_approximated_array = []
    coefs_array = []
    errors_array = []
    corr_matrixes = []
    for k in range(diffs.shape[0]):
        y_approximated, coefs, pcov = approximated(
            energies[1:13], res_all[k][i], error_sigma_all[k][i])
        y_approximated_array.append(y_approximated)
        coefs_array.append(coefs)
        errors_array.append(np.sqrt(abs(pcov.diagonal())))
        corr_matrixes.append(cov2corr(pcov))
        
    y_approximated_all.append(y_approximated_array)
    coefs_all.append(coefs_array)
    errors_all.append(errors_array)
    corr_matrixes_all.append(corr_matrixes)

corr_matrixes_all = np.array(corr_matrixes_all)

In [22]:
a = np.array(coefs_all).T[0]
b = np.array(coefs_all).T[1]
c = np.array(coefs_all).T[2]

In [23]:
plot_results(appr=True, ylim=3.5)

In [24]:
reindex = [0, 3, 1, 4, 2, 5]
coefs_df_real = pd.DataFrame(
    np.hstack((coefs_all[1], errors_all[1]))
)[reindex]
coefs_df_real.columns = ['a', r'$\Delta a$', 'b', r'$\Delta b$', 'c', r'$\Delta c$']

coefs_df_real = coefs_df_real.round(3)
coefs_df_real.index = names
coefs_df_real[r'$\tilde{a}$'] = (coefs_df_real['a']**2 + (1.6 * coefs_df_real['b'])**2 + (coefs_df_real['c'] / 1.6)**2)**0.5 
coefs_df_real[r'$\Delta \tilde{a}$'] = np.sqrt( (coefs_df_real['a']*coefs_df_real[r'$\Delta a$'])**2 + \
                                           (2.56*coefs_df_real['b']*coefs_df_real[r'$\Delta b$'])**2 + \
                                           (coefs_df_real['c']*coefs_df_real[r'$\Delta c$'] / 2.56)**2) / coefs_df_real[r'$\tilde{a}$']

coefs_df_real[r'$\Delta \tilde{a}$'] = np.sqrt(
    coefs_df_real[r'$\Delta \tilde{a}$']**2 + 2 * (
        1.6**2 * coefs_df_real['a'] * coefs_df_real['b'] / coefs_df_real[r'$\tilde{a}$']**2 *\
        corr_matrixes_all[1, :, 0, 1] * coefs_df_real[r'$\Delta a$'] * coefs_df_real[r'$\Delta b$'] +\
        
        coefs_df_real['a'] * coefs_df_real['c'] / (coefs_df_real[r'$\tilde{a}$']**2 * 1.6**2) *\
        corr_matrixes_all[1, :, 0, 2] * coefs_df_real[r'$\Delta a$'] * coefs_df_real[r'$\Delta c$'] +\

        coefs_df_real['b'] * coefs_df_real['c'] / coefs_df_real[r'$\tilde{a}$']**2 *\
        corr_matrixes_all[1, :, 1, 2] * coefs_df_real[r'$\Delta b$'] * coefs_df_real[r'$\Delta c$']
    )
)

In [25]:
coefs_df_real

a  $\Delta a$      b  $\Delta b$      c  $\Delta c$  \
R: 0-8.0 m      2.544       0.238  0.766       0.106  1.007       0.813   
R: 8.0-10.1 m   2.393       0.154  0.786       0.057  1.423       0.348   
R: 10.1-11.5 m  2.439       0.168  0.772       0.068  1.271       0.465   
R: 11.5-12.7 m  2.318       0.249  0.793       0.089  1.560       0.510   
R: 12.7-13.7 m  2.417       0.199  0.787       0.072  1.142       0.584   
R: 13.7-14.5 m  2.471       0.189  0.777       0.073  1.039       0.603   
R: 14.5-15.3 m  2.327       0.215  0.814       0.075  1.517       0.433   
R: 15.3-16.0 m  2.443       0.162  0.801       0.058  1.540       0.339   
R: 16.0-16.6 m  2.859       0.168  0.703       0.085  1.303       0.515   
R: 16.6-17.2 m  2.968       0.111  0.738       0.052  0.417       1.071   
R: 0-17.2 m     2.573       0.097  0.763       0.045  0.990       0.394   

                $\tilde{a}$  $\Delta \tilde{a}$  
R: 0-8.0 m         2.893120            0.048185  
R: 8.0-10.1 m      2.845873            0.031642  
R: 10.1-11.5 m     2.847011            0.032556  
R: 11.5-12.7 m     2.816665            0.048917  
R: 12.7-13.7 m     2.817253            0.041514  
R: 13.7-14.5 m     2.841316            0.040057  
R: 14.5-15.3 m     2.830215            0.043922  
R: 15.3-16.0 m     2.921841            0.034824  
R: 16.0-16.6 m     3.178406            0.035818  
R: 16.6-17.2 m     3.204877            0.026581  
R: 0-17.2 m        2.914367            0.015738

In [28]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=names,
        y=coefs_df_real[r'$\tilde{a}$'][:-1],
        marker=dict(
            color='darkblue',
        ),
        error_y=dict(
        type='data',
        width=10,
        array=coefs_df_real[r'$\Delta \tilde{a}$'],
        visible=True
        ),
    )
)

fig.add_hline(
    y=coefs_df_real[r'$\tilde{a}$'][-1],
    line=dict(
        dash='dash'
    )
)

fig.add_hrect(
    y0=coefs_df_real[r'$\tilde{a}$'][-1]-coefs_df_real[r'$\Delta \tilde{a}$'][-1],
    y1=coefs_df_real[r'$\tilde{a}$'][-1]+coefs_df_real[r'$\Delta \tilde{a}$'][-1],
    fillcolor="darkred",
    line_width=0,
    opacity=0.25,
)

# fig.add_hline(
#     y=2.857708,
#     line=dict(
#         dash='dash'
#     )
# )

# fig.add_hrect(
#     y0=2.857708-0.017573,
#     y1=2.857708+0.017573,
#     fillcolor="darkgreen",
#     line_width=0,
#     opacity=0.25,
# )

xaxis = dict(
    showline=True,
    ticks='outside',
    mirror=True,
    tick0=1,
    dtick=1,
    linecolor='black',
    showgrid=True,
    gridcolor='grey',
    gridwidth=0.25,
)

yaxis = lambda range: dict(
    showline=True,
    ticks='outside',
    mirror=True,
    linecolor='black',
    range=range,
    showgrid=True,
    gridcolor='grey',
    gridwidth=0.25,
    zeroline=True,
    zerolinecolor='black',
    zerolinewidth=0.25
)

fig.update_layout(
    xaxis_title="Region",
    yaxis_title=r'$\tilde{a}$',
    xaxis = xaxis,
    yaxis = yaxis([2.7, 3.32]),

    showlegend=False,
    height=500,
    width=950,
    font=dict(
            family="Times New Roman",
            size=16,
    ),
)

fig.show()
pio.write_image(fig, 'subdetectors/equidistant_subs/plots/atilde_vs_region.pdf', height=500, width=950)

In [27]:
coefs_df_real.to_csv("subdetectors/equidistant_subs/plots/atilde_vs_region.csv", index=False)